In [12]:
import pathlib

import ollama
import filetype

In [13]:
DATA_PATH = pathlib.Path("./data/")

In [7]:
def cleaning_image_filenames(dir: pathlib.Path):
    for path, dirs, files in dir.resolve().walk():
        for file in files:
            new_name = file.replace(' ', '_')
            (path / file).rename(new_name)

cleaning_image_filenames(DATA_PATH)

In [15]:
def get_output(file: pathlib.Path, lang: str) -> pathlib.Path:
    assert file.is_file(), "Checking if this is a file."
    return file.with_suffix(f'.{lang}.md')


prompt = 'Describe this image'
for path, dirs, files in DATA_PATH.resolve().walk():
    for file in files:
        if filetype.is_image(str(path / file)):
            r = ollama.chat(
                model="llava",
                messages=[{
                    'role': 'user',
                    'content': prompt,
                    'images': [(path / file).resolve()]
                }]
            )
            output_description = get_output(path / file, 'en')
            output_description.write_text(f"""
## Image `{file}`

![]({path / file})

## {prompt}

::: {{.border}}
{r['message']['content']}
:::

""")